In [1]:
#This code supports the work presented in the article "Infinitesimal Rigidity for Cubulated Manifolds" by Ludovico Battista.
#It contains parts written by Bruno Martelli, and can be found on his academic page.
#For more information about this, we suggest to read the articles 
#"Hyperbolic 4-manifolds with perfect circle-valued Morse functions" and "Hyperbolic 5-manifolds that fiber over S1".



# TECHNICAL GENERAL ROUTINES:

# Returns a list of length n with entries in 0, 1 (called a "binary" below) 
# that represents the number i as a binary number. Example: (4, 2) gives [0, 1, 0, 0]

def get_binary(n, i):
    answer = []
    i2 = i
    for j in range(n):
        if i2 % 2:
            answer.append(1)
            i2 = i2-1
        else:
            answer.append(0)
        i2 = i2/2
    return answer

In [2]:
# Returns the list of 2^n binaries with length n and entries 0, 1

def list_of_binaries(n):
    answer = []
    for i in range(2^n):
        new_vector = get_binary(n, i)
        answer.append(new_vector[:])
    return answer

In [4]:
# Returns the list of 2^n binaries with length n and entries 0, 1 with even number of ones
# This is useful because they will be the vertices of a certain even level

def list_of_even_binaries(n):
    answer = []
    for i in range(2^n):
        new_vector = get_binary(n, i)
        if sum(new_vector)%2==0:
            answer.append(new_vector[:])
    return answer

In [8]:
# Returns the list of 2^n binaries with length n and entries 0, 1 with odd number of ones
# This is useful because they will be the vertices of a certain odd level

def list_of_odd_binaries(n):
    answer = []
    for i in range(2^n):
        new_vector = get_binary(n, i)
        if sum(new_vector)%2==1:
            answer.append(new_vector[:])
    return answer

In [9]:
#switch 0 and 1

def switch(x):
    if x==0:
        return 1
    return 0

In [10]:
#get the state induced on the polytope corresponding to v \in Z/2^n.

def get_mirrored_state(S, C, v):
    S1=[]
    for ind in range(0,len(S)):
        if v[C[ind]] == 0:
            S1.append(S[ind])
        else:
            S1.append(switch(S[ind]))
    return S1

In [11]:
# Return a list of squares with their type
#This only works when you have a standard colouring and you change the state in a simple way, as in the article Battista, Martelli

import copy

def squares_and_types(G, C, S):
    num_faces=len(S)
    Squares=[]
    Squares_types=[]
    Vertices=list_of_even_binaries(max(C)+1)
    Pairs_done=[]
    for v in Vertices:
        Pairs_to_add=[]
        for ind1 in range(num_faces):
            for ind2 in range(ind1,num_faces):
                if G[ind1,ind2]==1:
                    v1=copy.deepcopy(v)
                    v1[C[ind1]]= switch(v1[C[ind1]])
                    v1[C[ind2]]= switch(v1[C[ind2]])
                    if not ([v,v1] in Pairs_done):
                        Pairs_to_add.append([v1,v])
                        Pairs_to_add.append([v,v1])
                        num_v=Vertices.index(v)
                        num_v1=Vertices.index(v1)
                        Square=[num_v*num_faces + ind1 + 1, num_v1*num_faces + ind2 + 1 , num_v1*num_faces + ind1 + 1, num_v*num_faces + ind2 + 1]
                        Squares.append(Square)
                        v_state=get_mirrored_state(S, C, v)
                        temp=[v_state[ind1],v_state[ind2]]
                        if set(temp)==set([0,1]):
                            Squares_types.append(1)
                        if set(temp)==set([0]):
                            Squares_types.append(2)
                        if set(temp)==set([1]):
                            Squares_types.append(3)
        Pairs_done=Pairs_done+Pairs_to_add
    return [Squares, Squares_types]

In [12]:
#Get the state induced on the polytope corresponding to v \in Z/2^n, when there are colours grouped.
#This means that you partition your colours, and when you mirror by a colour, you change the state of the facets 
#that have colour inside the partition of the colour you are mirroring by. See the article of Italiano, Martelli and Migliorini
#for more informations.

def get_mirrored_state_setcolored(S, C, v, set_colours):
    
    v1=[0 for x in v]
    for indexcount in range(0,len(v)):
        if v[indexcount]==1:
            set=[y for y in set_colours if indexcount in y][0]
            for indice in set:
                v1[indice]=v1[indice]+1
    v=[mod(x,2) for x in v1]
    S1=[]
    for ind in range(0,len(S)):
        if v[C[ind]] == 0:
            S1.append(S[ind])
        else:
            S1.append(switch(S[ind]))
    return S1

In [13]:
# Return a list of squares with their type when the colours are partitioned.

import copy

def squares_and_types_setcolored(G, C, S, set_colours):
    num_faces=len(S)
    Squares=[]
    Squares_types=[]
    Vertices=list_of_even_binaries(max(C)+1)
    Pairs_done=[]
    for v in Vertices:
        Pairs_to_add=[]
        for ind1 in range(num_faces):
            for ind2 in range(ind1,num_faces):
                if G[ind1,ind2]==1:
                    v1=copy.deepcopy(v)
                    v1[C[ind1]]= switch(v1[C[ind1]])
                    v1[C[ind2]]= switch(v1[C[ind2]])
                    if not ([v,v1] in Pairs_done):
                        Pairs_to_add.append([v1,v])
                        Pairs_to_add.append([v,v1])
                        num_v=Vertices.index(v)
                        num_v1=Vertices.index(v1)
                        Square=[num_v*num_faces + ind1 + 1, num_v1*num_faces + ind2 + 1 , num_v1*num_faces + ind1 + 1, num_v*num_faces + ind2 + 1]
                        Squares.append(Square)
                        v_state=get_mirrored_state_setcolored(S, C, v, set_colours)
                        v_state1=get_mirrored_state_setcolored(S, C, v1, set_colours)
                        temp=[v_state[ind1],v_state1[ind2],v_state1[ind1],v_state[ind2]]
                        
                        if temp==[0,0,1,1] or temp==[1,1,0,0]:
                            Squares_types.append(1)
                        elif temp==[0,1,1,0]:
                            Squares_types.append(2)
                        elif temp==[1,0,0,1]:
                            Squares_types.append(3)
                        elif temp==[1,1,1,1]:
                            Squares_types.append(1)
                        elif temp==[0,0,0,0]:
                            Squares_types.append(1)
                        else:
                            print('ERRORE'+str(temp)+str(v)+str(v1)+str([ind1,ind2]))
                            
        Pairs_done=Pairs_done+Pairs_to_add
    return [Squares, Squares_types]
                            
    

In [14]:
#This is used to print results in a convenient way for MATLAB.

def for_matlab(c):
    c=str(c)
    d=c.replace('], [', '; ')
    c=d.replace('[[', '[')
    d=c.replace(']]', '];')
    return(d)

In [33]:
# Quaternion multiplication

def quat_mult(z, w):
    (a,b,c,d,e,f,g,h) = (z[0], z[1], z[2], z[3], w[0], w[1], w[2], w[3])
    A = a*e - b*f - c*g - d*h
    B = a*f + b*e + c*h - d*g
    C = a*g + c*e + d*f - b*h
    D = a*h + d*e + b*g - c*f
    return [A,B,C,D]

# Returns the 8 elements of the quaternion group

def Q8():
    units = [[1, 0, 0, 0], [-1, 0, 0, 0], [0, 1, 0, 0], [0, -1, 0, 0], [0, 0, 1, 0], [0, 0, -1, 0], [0, 0, 0, 1], [0, 0, 0, -1]]
    return units

# Returns the binary tetrahedral group, that is the facets of the ideal 24-cell

def binary_tetrahedral():
    elements = [[1, 0, 0, 0], [1/2, 1/2, 1/2, 1/2], [-1/2, 1/2, 1/2, 1/2]]
    units = Q8()
    answer = []
    for q in elements:
        for p in units:
            new_element = quat_mult(p,q)
            answer.append(new_element[:])
    return answer

# Returns the binary icosahedral group, that is the facets of the 120-cell

def binary_icosahedral():
    tetra = binary_tetrahedral()
    phi = (1+sqrt(5))/2
    elements = [[1, 0, 0, 0], [0, 1/2, 1/(2*phi), phi/2], [0, 1/2, 1/(2*phi), -phi/2], [0, 1/2, -1/(2*phi), phi/2], [0, 1/2, -1/(2*phi), -phi/2]]
    answer = []
    valori_possibili = [0, 1, -1, 1/2, -1/2, phi/2, -phi/2, 1/(2*phi), -1/(2*phi)]
    for q in elements:
        for p in tetra:
            new_element = quat_mult(p,q)
            for i in range(4):
                for v in valori_possibili:
                    if abs(new_element[i] - v) < 0.1:
                        new_element[i] = v
            answer.append(new_element[:])
    return answer

In [37]:
#This is for the C24



# Returns the 24 vertices in R4 representing the facets of the 24-cell
# These are (pm 1, 0, 0, pm 1) and permutations
def C24_facets():
    facets = []
    for i in range(-1,2):
        for j in range(-1,2):
            for h in range(-1,2):
                for k in range(-1,2):
                    new_facet = [0,0,0,0]
                    new_facet[0] = i
                    new_facet[1] = j
                    new_facet[2] = h
                    new_facet[3] = k
                    if new_facet.count(0) == 2:
                        facets.append(new_facet[:])
    return facets


# Returns G for the ideal regular 24-cell    
    
def C24():
    G = Matrix(24,24)
    facets = C24_facets()
    for f in range(24):
        fc = facets[f]
        for g in range(24):
            gc = facets[g]
            dsquared = (fc[0] - gc[0])^2 + (fc[1] - gc[1])^2 + (fc[2] - gc[2])^2 + (fc[3] - gc[3])^2
            if dsquared == 2:
                G[f,g] = 1
    return G

def C24_colouring():
    colouring = [0, 1, 2, 2, 1, 0, 2, 1, 1, 2, 0, 0, 0, 0, 2, 1, 1, 2, 0, 1, 2, 2, 1, 0]
    return colouring

#These ones are the 63 states that define a perfect circle valued Morse function 
#(i.e.: a Morse function with only critical points of index 2) on the 24-cell with the standard colouring.
#See the article from Battista and Martelli for more information.
def C24_nice_states():
    Nice_states_C24=[[0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 0, 1, 1, 1, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 1, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 1, 1, 1, 1, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0],[0, 0, 0, 0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 0, 0],[0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0],[0, 0, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 0, 0, 0, 0]]
    return Nice_states_C24


In [31]:
#This is for P4

# Returns G for P4

def P4():
    G = Matrix(10,10)
    for i in range(5):
        for j in range(5):
            if (i-j) % 5 in [1,4]:
                G[i,j] = 1
            if (i-j) % 5 in [2,3]:
                G[i+5, j+5] = 1
            if i!=j:
                G[i,j+5] = 1
                G[i+5,j] = 1
    return G

# Returns the 5-colouring of P4:
    
def P4_colouring():
    colouring = [0, 1, 2, 3, 4, 0, 1, 2, 3, 4]
    return colouring

# Returns the base state of P4:

def P4_state():
    state = [1, 1, 1, 1, 1, 0, 0, 0, 0, 0]
    return state

In [35]:
#This is for C120


# Returns G for the right-angled 120-cell    

def C120():
    G = Matrix(120,120)
    ico = binary_icosahedral()
    phi = (1+sqrt(5))/2
    x = phi/2
    for i in range(120):
        v = ico[i]
        for j in range(i):
            w = ico[j]
            sp = sum([v[k] * w[k] for k in range(4)])
            if abs(sp - x) < 0.1:
                G[i,j] = 1
                G[j,i] = 1
    return G

def C120_state():
    base_state = [1, 1, 1, 1, 0, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1]
    state = []
    for i in range(5):
        for j in range(24):
            state.append(base_state[j])
    return state

# Returns the 5-colouring of the 120-cell:

def C120_colouring():
    answer = []
    for i in range(5):
        for j in range(24):
            answer.append(i)
    return answer

In [42]:
#This is for ideal regular octahedron


# Returns G for the ideal regular octahedron

def octa():
    G = matrix(8,8)
    for f in range(8):
        for g in range(8):
            if (f <= 3 and g <= 3) or (f >= 4 and g >= 4):
                if (g-f) % 4 == 1 or (g-f) % 4 == 3:
                    G[f,g] = 1
            if abs (g-f) == 4: G[f,g] = 1
    return G

# Returns the 2-colouring of the ideal regular octahedron:
    
def octa_colouring():
    colouring = [0, 1, 0, 1, 1, 0, 1, 0]
    return colouring


# Returns the base state of the ideal regular octahedron:

def octa_state():
    state = [1, 1, 1, 0, 1, 0, 0, 0]
    return state

In [43]:
#This is for P5 with the conventions of Ludovico Battista


# Returns G for P5

def P5_Ludo():
    G = matrix(16,16)
    x=list_of_even_binaries(5)
    for ind1 in range(0,16):
        for ind2 in range(0,16):
            if abs( vector(x[ind1]) -vector(x[ind2]) ) ==sqrt(2):
                G[ind1,ind2]=1
    
    return G

# Returns the 8-colouring of P5:
    
def P5_colouring_Ludo():
    colouring = [0, 3, 1, 2, 2, 1, 3, 0, 4, 6, 7, 5, 5, 7, 6, 4]
    return colouring

# Returns the base state of P5:

def P5_state_Ludo():
    state = [0,1,0,0,1,1,0,1,0,0,0,0,1,1,1,1]
    return state

def P5_sets():
    sets = [[0,4],[1,5],[2,6],[3,7]]
    return sets

In [38]:
#This is an example of how to obtain the squares and their types:

G=C24()
C=C24_colouring()
S=C24_nice_states()[0]
[a,b]=squares_and_types(G, C, S)


print(for_matlab(a))
print(for_matlab(b))


[1, 26, 25, 2; 1, 51, 49, 3; 1, 52, 49, 4; 1, 29, 25, 5; 1, 55, 49, 7; 1, 32, 25, 8; 1, 33, 25, 9; 1, 58, 49, 10; 2, 75, 74, 3; 2, 76, 74, 4; 2, 30, 26, 6; 2, 79, 74, 7; 2, 35, 26, 11; 2, 36, 26, 12; 2, 87, 74, 15; 3, 77, 75, 5; 3, 54, 51, 6; 3, 80, 75, 8; 3, 59, 51, 11; 3, 61, 51, 13; 3, 88, 75, 16; 4, 77, 76, 5; 4, 54, 52, 6; 4, 81, 76, 9; 4, 60, 52, 12; 4, 62, 52, 14; 4, 89, 76, 17; 5, 30, 29, 6; 5, 82, 77, 10; 5, 37, 29, 13; 5, 38, 29, 14; 5, 90, 77, 18; 6, 63, 54, 15; 6, 40, 30, 16; 6, 41, 30, 17; 6, 66, 54, 18; 7, 80, 79, 8; 7, 81, 79, 9; 7, 59, 55, 11; 7, 60, 55, 12; 7, 67, 55, 19; 7, 92, 79, 20; 8, 82, 80, 10; 8, 35, 32, 11; 8, 37, 32, 13; 8, 43, 32, 19; 8, 93, 80, 21; 9, 82, 81, 10; 9, 36, 33, 12; 9, 38, 33, 14; 9, 43, 33, 19; 9, 94, 81, 22; 10, 61, 58, 13; 10, 62, 58, 14; 10, 67, 58, 19; 10, 95, 82, 23; 11, 63, 59, 15; 11, 40, 35, 16; 11, 44, 35, 20; 11, 69, 59, 21; 12, 63, 60, 15; 12, 41, 36, 17; 12, 44, 36, 20; 12, 70, 60, 22; 13, 40, 37, 16; 13, 66, 61, 18; 13, 69, 61, 21;

In [45]:
#Another example where the colours are partitioned

[a,b]=squares_and_types_setcolored(P5_Ludo(), P5_colouring_Ludo(), P5_state_Ludo(), P5_sets())

print(for_matlab(a))
print(for_matlab(b))

[1, 66, 65, 2; 1, 19, 17, 3; 1, 36, 33, 4; 1, 37, 33, 5; 1, 22, 17, 6; 1, 71, 65, 7; 1, 137, 129, 9; 1, 522, 513, 10; 1, 1035, 1025, 11; 1, 269, 257, 13; 2, 83, 82, 3; 2, 100, 98, 4; 2, 101, 98, 5; 2, 86, 82, 6; 2, 72, 66, 8; 2, 201, 194, 9; 2, 586, 578, 10; 2, 332, 322, 12; 2, 1102, 1090, 14; 3, 52, 51, 4; 3, 53, 51, 5; 3, 87, 83, 7; 3, 24, 19, 8; 3, 153, 147, 9; 3, 1051, 1043, 11; 3, 284, 275, 12; 3, 543, 531, 15; 4, 54, 52, 6; 4, 103, 100, 7; 4, 40, 36, 8; 4, 554, 548, 10; 4, 1067, 1060, 11; 4, 300, 292, 12; 4, 176, 164, 16; 5, 54, 53, 6; 5, 103, 101, 7; 5, 40, 37, 8; 5, 169, 165, 9; 5, 301, 293, 13; 5, 1070, 1061, 14; 5, 559, 549, 15; 6, 87, 86, 7; 6, 24, 22, 8; 6, 538, 534, 10; 6, 285, 278, 13; 6, 1054, 1046, 14; 6, 160, 150, 16; 7, 72, 71, 8; 7, 1099, 1095, 11; 7, 333, 327, 13; 7, 591, 583, 15; 7, 208, 199, 16; 8, 268, 264, 12; 8, 1038, 1032, 14; 8, 527, 520, 15; 8, 144, 136, 16; 9, 650, 649, 10; 9, 1163, 1161, 11; 9, 396, 393, 12; 9, 397, 393, 13; 9, 1166, 1161, 14; 9, 655, 649,